# Extract Sequences from pdb and save parts

In [6]:
!pip install biopython

In [1]:
import os
import json
from Bio.PDB import PDBParser
from Bio.Seq import Seq
from Bio import SeqIO

def load_jsonl_in_dict(jsonl_file_path):
    # Initialize a list to store all JSON objects
    data = []

    # Read the .jsonl file and parse each line
    with open(jsonl_file_path, 'r') as file:
        for line in file:
            # Load each JSON object from the line
            data.append(json.loads(line.strip()))

    # Convert to a dictionary if needed (e.g., if the JSONL has a key-value structure)
    # Example: Assuming each JSON object has a unique 'id' field
    data_dict = {item['id']: item for item in data if 'id' in item}

    return data_dict


def extract_sequence(file_path):
    # Load the PDB file
    pdb_file = file_path
    parser = PDBParser()
    structure = parser.get_structure(pdb_file.split("/")[-1].replace(".pdb", ""), pdb_file)

    # Define the three-letter to one-letter amino acid conversion dictionary
    three_to_one = {
        'ALA': 'A', 'ARG': 'R', 'ASN': 'N', 'ASP': 'D', 'CYS': 'C',
        'GLN': 'Q', 'GLU': 'E', 'GLY': 'G', 'HIS': 'H', 'ILE': 'I',
        'LEU': 'L', 'LYS': 'K', 'MET': 'M', 'PHE': 'F', 'PRO': 'P',
        'SER': 'S', 'THR': 'T', 'TRP': 'W', 'TYR': 'Y', 'VAL': 'V'
    }

    # Extract sequence
    sequence = []
    for model in structure:
        for chain in model:
            for residue in chain:
                # Only consider standard amino acids
                if residue.id[0] == " " and residue.resname in three_to_one:
                    # Append the one-letter code
                    sequence.append(three_to_one[residue.resname])

    # Join the sequence list into a single string
    one_letter_sequence = ''.join(sequence)

    return one_letter_sequence

In [13]:
d = load_jsonl_in_dict("../data/train.jsonl")

In [15]:
counter = 0
for k,v in d.items():
    print(k,v)
    counter += 1
    if counter == 5:
        break

1es5-A {'id': '1es5-A', 'sequence': 'VTKPTIAAVGGYAMNNGTGTTLYTKAADTRRSTGSTTKIMTAKVVLAQSNLNLDAKVTIQKAYSDYVVANNASQAHLIVGDKVTVRQLLYGLMLPSGCDAAYALADKYGSGSTRAARVKSFIGKMNTAATNLGLHNTHFDSFDGIGNGANYSTPRDLTKIASSAMKNSTFRTVVKTKAYTAKTVTKTGSIRTMDTWKNTNGLLSSYSGAIGVKTGAGPEAKYCLVFAATRGGKTVIGTVLASTSIPARESDATKIMNYGFAL', 'label': 'CCCCCCCCCEEEEEECCCCCEEEEECCCCCECCHHHHHHHHHHHHHCCCCCCCCCEEECCHHHHHHHHHCCCCCCCCCCCCEEEHHHHHHHHHCCCCHHHHHHHHHHHCCCCCHHHHHHHHHHHHHHHHHHCCCCCCECCCCCCCCCCCCEECHHHHHHHHHHHCCCHHHHHHHCCCEECCEEECCCCCEEECCCEECCCCHHHHCCCEEEEEEEEECCCEEEEEEEEEECCEEEEEEEEEECCHHHHHHHHHHHHHHHHHC', 'resolved': '0011111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111'}
2a6h-E {'id': '2a6h-E', 'sequence': 'MAEPGIDKLFGMVDSKYRLTVVVAKRAQQLLRHGFKNTVLEPEERPKMQTLEGLFDDPNAETWAMKELLTGRLVFGENLVPEDRLQKEMERIYPGEREE', 'label

In [28]:
seq_pdb = extract_sequence("../data/train_pdbs/1es5-A.pdb")
print("PDB: ", seq_pdb)

KPTIAAVGGYAMNNGTGTTLYTKAADTRRSTGSTTKIMTAKVVLAQSNLNLDAKVTIQKAYSDYVVANNASQAHLIVGDKVTVRQLLYGLMLPSGCDAAYALADKYGSGSTRAARVKSFIGKMNTAATNLGLHNTHFDSFDGIGNGANYSTPRDLTKIASSAMKNSTFRTVVKTKAYTAKTVTKTGSIRTMDTWKNTNGLLSSYSGAIGVKTGAGPEAKYCLVFAATRGGKTVIGTVLASTSIPARESDATKIMNYGFAL


In [29]:
print("JSONL:", d["1es5-A"]["sequence"])

JSONL: VTKPTIAAVGGYAMNNGTGTTLYTKAADTRRSTGSTTKIMTAKVVLAQSNLNLDAKVTIQKAYSDYVVANNASQAHLIVGDKVTVRQLLYGLMLPSGCDAAYALADKYGSGSTRAARVKSFIGKMNTAATNLGLHNTHFDSFDGIGNGANYSTPRDLTKIASSAMKNSTFRTVVKTKAYTAKTVTKTGSIRTMDTWKNTNGLLSSYSGAIGVKTGAGPEAKYCLVFAATRGGKTVIGTVLASTSIPARESDATKIMNYGFAL


# Save the parts

In [ ]:
from tqdm import tqdm
folder = "../data/train_pdbs/"
files = os.listdir(folder)

pdb_seqs = []
counter = 0
part_no = 0
for file in tqdm(files):
    pid = file.replace(".pdb", "")
    seq_pdb = extract_sequence(folder + file)
    pdb_seqs.append((pid, seq_pdb))
    counter += 1
    if counter % 1000 == 0:
        with open(f"../data/parts/train_{part_no}.csv", "w") as wf:
            for pid, seq in pdb_seqs:
                wf.write(f"{pid};{seq}\n")
            part_no += 1
        pdb_seqs = []
    

  0%|          | 0/9712 [00:00<?, ?it/s]C:\Users\kokta\anaconda3\envs\esm2ft\lib\site-packages\Bio\PDB\StructureBuilder.py:100: PDBConstructionWarning: WARNING: Chain A is discontinuous at line 5666.
  warnings.warn(
C:\Users\kokta\anaconda3\envs\esm2ft\lib\site-packages\Bio\PDB\StructureBuilder.py:100: PDBConstructionWarning: WARNING: Chain B is discontinuous at line 5698.
  warnings.warn(
C:\Users\kokta\anaconda3\envs\esm2ft\lib\site-packages\Bio\PDB\StructureBuilder.py:100: PDBConstructionWarning: WARNING: Chain A is discontinuous at line 5730.
  warnings.warn(
C:\Users\kokta\anaconda3\envs\esm2ft\lib\site-packages\Bio\PDB\StructureBuilder.py:100: PDBConstructionWarning: WARNING: Chain B is discontinuous at line 5832.
  warnings.warn(
  0%|          | 2/9712 [00:00<09:11, 17.59it/s]C:\Users\kokta\anaconda3\envs\esm2ft\lib\site-packages\Bio\PDB\StructureBuilder.py:100: PDBConstructionWarning: WARNING: Chain A is discontinuous at line 9619.
  warnings.warn(
C:\Users\kokta\anaconda3\en

  0%|          | 19/9712 [00:01<18:52,  8.56it/s]C:\Users\kokta\anaconda3\envs\esm2ft\lib\site-packages\Bio\PDB\StructureBuilder.py:100: PDBConstructionWarning: WARNING: Chain A is discontinuous at line 915.
  warnings.warn(
C:\Users\kokta\anaconda3\envs\esm2ft\lib\site-packages\Bio\PDB\StructureBuilder.py:100: PDBConstructionWarning: WARNING: Chain B is discontinuous at line 920.
  warnings.warn(
C:\Users\kokta\anaconda3\envs\esm2ft\lib\site-packages\Bio\PDB\StructureBuilder.py:100: PDBConstructionWarning: WARNING: Chain C is discontinuous at line 939.
  warnings.warn(
  0%|          | 22/9712 [00:02<15:58, 10.11it/s]C:\Users\kokta\anaconda3\envs\esm2ft\lib\site-packages\Bio\PDB\StructureBuilder.py:100: PDBConstructionWarning: WARNING: Chain A is discontinuous at line 3135.
  warnings.warn(
C:\Users\kokta\anaconda3\envs\esm2ft\lib\site-packages\Bio\PDB\StructureBuilder.py:100: PDBConstructionWarning: WARNING: Chain B is discontinuous at line 3314.
  warnings.warn(
C:\Users\kokta\anaco

  0%|          | 37/9712 [00:03<14:47, 10.90it/s]C:\Users\kokta\anaconda3\envs\esm2ft\lib\site-packages\Bio\PDB\StructureBuilder.py:100: PDBConstructionWarning: WARNING: Chain A is discontinuous at line 1080.
  warnings.warn(
C:\Users\kokta\anaconda3\envs\esm2ft\lib\site-packages\Bio\PDB\StructureBuilder.py:100: PDBConstructionWarning: WARNING: Chain B is discontinuous at line 1148.
  warnings.warn(
C:\Users\kokta\anaconda3\envs\esm2ft\lib\site-packages\Bio\PDB\StructureBuilder.py:100: PDBConstructionWarning: WARNING: Chain C is discontinuous at line 1171.
  warnings.warn(
C:\Users\kokta\anaconda3\envs\esm2ft\lib\site-packages\Bio\PDB\StructureBuilder.py:100: PDBConstructionWarning: WARNING: Chain A is discontinuous at line 3880.
  warnings.warn(
C:\Users\kokta\anaconda3\envs\esm2ft\lib\site-packages\Bio\PDB\StructureBuilder.py:100: PDBConstructionWarning: WARNING: Chain B is discontinuous at line 3912.
  warnings.warn(
C:\Users\kokta\anaconda3\envs\esm2ft\lib\site-packages\Bio\PDB\Str

C:\Users\kokta\anaconda3\envs\esm2ft\lib\site-packages\Bio\PDB\StructureBuilder.py:100: PDBConstructionWarning: WARNING: Chain A is discontinuous at line 14063.
  warnings.warn(
C:\Users\kokta\anaconda3\envs\esm2ft\lib\site-packages\Bio\PDB\StructureBuilder.py:100: PDBConstructionWarning: WARNING: Chain B is discontinuous at line 14757.
  warnings.warn(
  1%|          | 59/9712 [00:04<10:52, 14.79it/s]C:\Users\kokta\anaconda3\envs\esm2ft\lib\site-packages\Bio\PDB\StructureBuilder.py:100: PDBConstructionWarning: WARNING: Chain A is discontinuous at line 4509.
  warnings.warn(
C:\Users\kokta\anaconda3\envs\esm2ft\lib\site-packages\Bio\PDB\StructureBuilder.py:100: PDBConstructionWarning: WARNING: Chain C is discontinuous at line 4521.
  warnings.warn(
C:\Users\kokta\anaconda3\envs\esm2ft\lib\site-packages\Bio\PDB\StructureBuilder.py:100: PDBConstructionWarning: WARNING: Chain A is discontinuous at line 4533.
  warnings.warn(
C:\Users\kokta\anaconda3\envs\esm2ft\lib\site-packages\Bio\PDB\S

  1%|          | 71/9712 [00:05<14:56, 10.75it/s]C:\Users\kokta\anaconda3\envs\esm2ft\lib\site-packages\Bio\PDB\StructureBuilder.py:100: PDBConstructionWarning: WARNING: Chain B is discontinuous at line 2684.
  warnings.warn(
C:\Users\kokta\anaconda3\envs\esm2ft\lib\site-packages\Bio\PDB\StructureBuilder.py:100: PDBConstructionWarning: WARNING: Chain A is discontinuous at line 2709.
  warnings.warn(
  1%|          | 73/9712 [00:06<18:03,  8.90it/s]C:\Users\kokta\anaconda3\envs\esm2ft\lib\site-packages\Bio\PDB\StructureBuilder.py:100: PDBConstructionWarning: WARNING: Chain 1 is discontinuous at line 5220.
  warnings.warn(
C:\Users\kokta\anaconda3\envs\esm2ft\lib\site-packages\Bio\PDB\StructureBuilder.py:100: PDBConstructionWarning: WARNING: Chain 3 is discontinuous at line 5230.
  warnings.warn(
C:\Users\kokta\anaconda3\envs\esm2ft\lib\site-packages\Bio\PDB\StructureBuilder.py:100: PDBConstructionWarning: WARNING: Chain 1 is discontinuous at line 5241.
  warnings.warn(
C:\Users\kokta\an

...

 83%|████████▎ | 8057/9712 [25:36<04:58,  5.54it/s]C:\Users\kokta\anaconda3\envs\esm2ft\lib\site-packages\Bio\PDB\StructureBuilder.py:100: PDBConstructionWarning: WARNING: Chain A is discontinuous at line 3883.
  warnings.warn(
C:\Users\kokta\anaconda3\envs\esm2ft\lib\site-packages\Bio\PDB\StructureBuilder.py:100: PDBConstructionWarning: WARNING: Chain B is discontinuous at line 4401.
  warnings.warn(
 83%|████████▎ | 8058/9712 [25:36<04:32,  6.06it/s]C:\Users\kokta\anaconda3\envs\esm2ft\lib\site-packages\Bio\PDB\StructureBuilder.py:100: PDBConstructionWarning: WARNING: Chain A is discontinuous at line 5307.
  warnings.warn(
C:\Users\kokta\anaconda3\envs\esm2ft\lib\site-packages\Bio\PDB\StructureBuilder.py:100: PDBConstructionWarning: WARNING: Chain B is discontinuous at line 5328.
  warnings.warn(
C:\Users\kokta\anaconda3\envs\esm2ft\lib\site-packages\Bio\PDB\StructureBuilder.py:100: PDBConstructionWarning: WARNING: Chain A is discontinuous at line 5349.
  warnings.warn(
C:\Users\kokt

 83%|████████▎ | 8076/9712 [25:38<04:52,  5.58it/s]C:\Users\kokta\anaconda3\envs\esm2ft\lib\site-packages\Bio\PDB\StructureBuilder.py:100: PDBConstructionWarning: WARNING: Chain A is discontinuous at line 2855.
  warnings.warn(
C:\Users\kokta\anaconda3\envs\esm2ft\lib\site-packages\Bio\PDB\StructureBuilder.py:100: PDBConstructionWarning: WARNING: Chain B is discontinuous at line 3055.
  warnings.warn(
C:\Users\kokta\anaconda3\envs\esm2ft\lib\site-packages\Bio\PDB\StructureBuilder.py:100: PDBConstructionWarning: WARNING: Chain A is discontinuous at line 2521.
  warnings.warn(
C:\Users\kokta\anaconda3\envs\esm2ft\lib\site-packages\Bio\PDB\StructureBuilder.py:100: PDBConstructionWarning: WARNING: Chain B is discontinuous at line 2632.
  warnings.warn(
 83%|████████▎ | 8078/9712 [25:38<03:51,  7.07it/s]C:\Users\kokta\anaconda3\envs\esm2ft\lib\site-packages\Bio\PDB\StructureBuilder.py:100: PDBConstructionWarning: WARNING: Chain A is discontinuous at line 8469.
  warnings.warn(
C:\Users\kokt

 83%|████████▎ | 8089/9712 [25:41<05:47,  4.68it/s]C:\Users\kokta\anaconda3\envs\esm2ft\lib\site-packages\Bio\PDB\StructureBuilder.py:100: PDBConstructionWarning: WARNING: Chain A is discontinuous at line 16606.
  warnings.warn(
C:\Users\kokta\anaconda3\envs\esm2ft\lib\site-packages\Bio\PDB\StructureBuilder.py:100: PDBConstructionWarning: WARNING: Chain D is discontinuous at line 16630.
  warnings.warn(
C:\Users\kokta\anaconda3\envs\esm2ft\lib\site-packages\Bio\PDB\StructureBuilder.py:100: PDBConstructionWarning: WARNING: Chain A is discontinuous at line 16643.
  warnings.warn(
C:\Users\kokta\anaconda3\envs\esm2ft\lib\site-packages\Bio\PDB\StructureBuilder.py:100: PDBConstructionWarning: WARNING: Chain D is discontinuous at line 17093.
  warnings.warn(
 83%|████████▎ | 8090/9712 [25:41<06:59,  3.87it/s]C:\Users\kokta\anaconda3\envs\esm2ft\lib\site-packages\Bio\PDB\StructureBuilder.py:100: PDBConstructionWarning: WARNING: Chain A is discontinuous at line 25063.
  warnings.warn(
C:\Users

 83%|████████▎ | 8101/9712 [25:44<10:53,  2.47it/s]C:\Users\kokta\anaconda3\envs\esm2ft\lib\site-packages\Bio\PDB\StructureBuilder.py:100: PDBConstructionWarning: WARNING: Chain A is discontinuous at line 6046.
  warnings.warn(
C:\Users\kokta\anaconda3\envs\esm2ft\lib\site-packages\Bio\PDB\StructureBuilder.py:100: PDBConstructionWarning: WARNING: Chain C is discontinuous at line 6426.
  warnings.warn(
C:\Users\kokta\anaconda3\envs\esm2ft\lib\site-packages\Bio\PDB\StructureBuilder.py:100: PDBConstructionWarning: WARNING: Chain D is discontinuous at line 6516.
  warnings.warn(
 83%|████████▎ | 8102/9712 [25:45<09:22,  2.86it/s]C:\Users\kokta\anaconda3\envs\esm2ft\lib\site-packages\Bio\PDB\StructureBuilder.py:100: PDBConstructionWarning: WARNING: Chain A is discontinuous at line 8516.
  warnings.warn(
C:\Users\kokta\anaconda3\envs\esm2ft\lib\site-packages\Bio\PDB\StructureBuilder.py:100: PDBConstructionWarning: WARNING: Chain B is discontinuous at line 8520.
  warnings.warn(
C:\Users\kokt

C:\Users\kokta\anaconda3\envs\esm2ft\lib\site-packages\Bio\PDB\StructureBuilder.py:100: PDBConstructionWarning: WARNING: Chain A is discontinuous at line 10146.
  warnings.warn(
C:\Users\kokta\anaconda3\envs\esm2ft\lib\site-packages\Bio\PDB\StructureBuilder.py:100: PDBConstructionWarning: WARNING: Chain B is discontinuous at line 10154.
  warnings.warn(
C:\Users\kokta\anaconda3\envs\esm2ft\lib\site-packages\Bio\PDB\StructureBuilder.py:100: PDBConstructionWarning: WARNING: Chain A is discontinuous at line 10157.
  warnings.warn(
C:\Users\kokta\anaconda3\envs\esm2ft\lib\site-packages\Bio\PDB\StructureBuilder.py:100: PDBConstructionWarning: WARNING: Chain B is discontinuous at line 10259.
  warnings.warn(
 84%|████████▎ | 8114/9712 [25:47<05:55,  4.50it/s]C:\Users\kokta\anaconda3\envs\esm2ft\lib\site-packages\Bio\PDB\StructureBuilder.py:100: PDBConstructionWarning: WARNING: Chain A is discontinuous at line 3828.
  warnings.warn(
C:\Users\kokta\anaconda3\envs\esm2ft\lib\site-packages\Bio\P